## Notebook for testing Scikit Learn models

#### Imports

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
pd.set_option('display.float_format', lambda x: '%.4f' % x)
import seaborn as sns
sns.set_context("paper", font_scale=1.3)
sns.set_style('white')
import warnings
warnings.filterwarnings('ignore')
import datetime
import matplotlib.ticker as tkr
import math
import keras
import os.path
import sklearn as sk
import seaborn as sns
from scipy import stats
from statsmodels.tsa.stattools import adfuller
from sklearn import preprocessing
from statsmodels.tsa.stattools import pacf
%matplotlib inline
from sklearn.preprocessing import OneHotEncoder
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import label_binarize
from sklearn.metrics import multilabel_confusion_matrix, max_error
from sklearn.metrics import roc_curve, roc_auc_score, accuracy_score, precision_score, confusion_matrix, recall_score 
from sklearn.metrics import f1_score, auc, matthews_corrcoef, mean_absolute_error, mean_squared_error
from sklearn.metrics import classification_report
from sklearn.feature_selection import SelectPercentile, f_regression, mutual_info_regression, SelectKBest


from os import path
from time import time
from IPython.display import display
from IPython.display import SVG
from sklearn.model_selection import train_test_split

from numpy.random import seed
seed(20)
import tensorflow as tf
from keras import backend as K
from keras.wrappers.scikit_learn import KerasRegressor
from sklearn.model_selection import cross_val_score
from scipy.stats import pearsonr
import lightgbm as lgb

from sklearn.linear_model import RidgeCV, LogisticRegression
from sklearn.svm import LinearSVR
from sklearn.ensemble import RandomForestRegressor
from xgboost.sklearn import XGBRegressor


from sklearn.ensemble import ExtraTreesRegressor

from sklearn.svm import SVR
from math import sqrt
from sklearn.metrics import r2_score, max_error

from sklearn.svm import LinearSVR

from sklearn.feature_selection import SelectFromModel
    
from sklearn.utils import shuffle

from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import VotingRegressor
import xgboost as xgb
from sklearn.metrics.scorer import make_scorer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import cross_validate, TimeSeriesSplit

pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True)

C:\Users\Austin\Anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


#### Helper Methods

In [2]:
class Logger(object):
    def __init__(self):
        self.terminal = sys.stdout
        self.log = open("All_Classifierq.log", "a")

    def write(self, message):
        self.terminal.write(message)
        self.log.write(message)  

    def flush(self):
        #this flush method is needed for python 3 compatibility.
        #this handles the flush command by doing nothing.
        #you might want to specify some extra behavior here.
        self.acquire()
        try:
            if self.stream and hasattr(self.stream, "flush"):
                self.stream.flush()
        finally:
            self.release()

import sys

def spcc(y_true, y_pred, **kwargs):
    corr, _ = pearsonr(y_true, y_pred)
    return corr
    
    
def windowed_dataset(series, window_size, batch_size, shuffle_buffer):
    dataset = tf.data.Dataset.from_tensor_slices(series)
    dataset = dataset.window(window_size + 1, shift=1, drop_remainder=True)
    dataset = dataset.flat_map(lambda window: window.batch(window_size + 1))
    #dataset = dataset.shuffle(shuffle_buffer).map(lambda window: (window[:-1], window[-1]))
    dataset = dataset.map(lambda window: (window[:-1], window[-1]))
    dataset = dataset.batch(batch_size).prefetch(1)
    return dataset
    
#Takes a dataframe with the holiday field and returns encoded dataframe.
def onehotholiday(select):
    X_2 = select[['Holiday']]
    # TODO: create a OneHotEncoder object, and fit it to all of X
    # 1. INSTANTIATE
    enc = preprocessing.OneHotEncoder(sparse=False)
    
    # 2. FIT
    enc.fit(X_2)
    
    # 3. Transform
    onehotlabels = enc.transform(X_2)
    # creating a list of column names 
    column_values = []
    for i in range(np.shape(onehotlabels)[1]):
            column_values.append('A'+str(i))

    # creating the dataframe 
    onehotholiday = pd.DataFrame(data = onehotlabels,columns = column_values)

    dataset = select.drop(columns=['Holiday'])
    dataset = select.join(onehotholiday)
    df1 = dataset.pop('2to5')
    dataset['2to5']=df1 # add b series as a 'new' column
    dataset2=dataset
    dataset2 = dataset2.drop(columns=['Holiday'])
    return dataset2
    
def onehotholidaydiff(select, col):
    X_2 = select[['Holiday']]
    # TODO: create a OneHotEncoder object, and fit it to all of X
    # 1. INSTANTIATE
    enc = preprocessing.OneHotEncoder(sparse=False)
    
    # 2. FIT
    enc.fit(X_2)
    
    # 3. Transform
    onehotlabels = enc.transform(X_2)
    # creating a list of column names 
    column_values = []
    for i in range(np.shape(onehotlabels)[1]):
            column_values.append('A'+str(i))

    # creating the dataframe 
    onehotholiday = pd.DataFrame(data = onehotlabels,columns = column_values)

    dataset = select.drop(columns=['Holiday'])
    dataset = select.join(onehotholiday)
    df1 = dataset.pop(col)
    dataset[col]=df1 # add b series as a 'new' column
    dataset2=dataset
    dataset2 = dataset2.drop(columns=['Holiday'])
    return dataset2
    
    

def diff_add_lookback(dataset, look_back, df, col):
    for i in range(len(dataset)-look_back):
        a = dataset[i:(i+look_back)][col]
        a = a.values
        for j in range(len(a)):
            df[j][i]= a[j]
    return df

def add_lookback(dataset, look_back, df):
    for i in range(len(dataset)-look_back):
        a = dataset[i:(i+look_back)]['2to5']
        a = a.values
        for j in range(len(a)):
            df[j][i]= a[j]
    return df

#### Initilization of all tested models

from sklearn.neural_network import MLPRegressor
nn =  MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42) 
stack_nn = MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42)
from sklearn.neighbors import KNeighborsRegressor

neigh = KNeighborsRegressor(n_neighbors=7)
stack_neigh = KNeighborsRegressor(n_neighbors=7)

from mlxtend.regressor import StackingCVRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.linear_model import Ridge
LR = LinearRegression()
rid = Ridge(alpha=1.0)
et = ExtraTreesRegressor(n_estimators=1000, random_state=0)

stack = StackingCVRegressor(regressors=(LR, rid, et, stack_neigh, stack_nn),
                            meta_regressor=rid, 
                            random_state=42,
                            use_features_in_secondary=True)

lgbm = lgb.LGBMRegressor(num_leaves=31,
                        learning_rate=0.05,
                        n_estimators=1000)

XGBModel = XGBRegressor(learning_rate =0.05,
 n_estimators=2000,
 max_depth=5,
 min_child_weight=1,
 gamma=0.1,
 subsample=0.8,
 colsample_bytree=0.8,
 objective= 'reg:squarederror',
 nthread=5,
 scale_pos_weight=1,
 seed=21,
 eval_metric = ['mae'])

ETCModel  = ExtraTreesRegressor(n_estimators=1000, random_state=0)

from sklearn.gaussian_process import GaussianProcessRegressor
gpr = GaussianProcessRegressor()

from sklearn.linear_model import SGDRegressor
from sklearn.linear_model import LassoCV
Lcv = LassoCV(cv=5, random_state=0)
LR = LinearRegression()
SGD = SGDRegressor(max_iter=1000, tol=1e-3)

from sklearn.neighbors import KNeighborsRegressor
neigh = KNeighborsRegressor(n_neighbors=7)


from sklearn.linear_model import Ridge
ridge = Ridge(alpha=1.0)

from sklearn.linear_model import ElasticNetCV
els = ElasticNetCV(cv=10, random_state=0,max_iter=100000)    

from sklearn.tree import DecisionTreeRegressor   
dt = DecisionTreeRegressor(random_state=0,criterion="mae") 

from sklearn.kernel_ridge import KernelRidge
kridge = KernelRidge()

from sklearn.linear_model import BayesianRidge
bridge = BayesianRidge()

from sklearn.svm import SVR, NuSVR, LinearSVR
svr = SVR()
nusvr = NuSVR()
linsvr = LinearSVR()

from sklearn.ensemble import GradientBoostingRegressor
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import VotingRegressor
from sklearn.linear_model import SGDRegressor
reg1 = GradientBoostingRegressor(random_state=1, n_estimators=10)
reg2 = RandomForestRegressor(random_state=1, n_estimators=10)
reg3 = LinearRegression()
reg4 = DecisionTreeRegressor(random_state=0,criterion="mae")
reg5 = SGDRegressor(max_iter=1000, tol=1e-3)

VR = VotingRegressor(estimators=[('gb', reg1), ('rf', reg2), ('lr', reg3), ('dt',reg4), ('sgd',reg5)])


from sklearn.neural_network import MLPRegressor
nn = MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42)

tss = TimeSeriesSplit(n_splits = 10)

from sklearn.multioutput import MultiOutputRegressor, RegressorChain
multireg = MultiOutputRegressor(ridge)
regchain = RegressorChain(ridge)

## Single Day Forecast

#### Training and testing all models vs. an increasing number of features.

In [4]:
np.random.seed(42)w
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason',
                         0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                         'WeeklyBusyness','2to5']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

lb_data = add_lookback(data, lookback, df)
lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholiday(lb_data)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

sys.stdout.flush()

clflist=[stack,VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,kridge, 
         Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  

recording = pd.DataFrame(clflist,columns=['Model'])

#
scoring = {
    'max' : 'max_error',
    'mae': 'neg_mean_absolute_error',
    'mse' : 'neg_mean_squared_error',
           'custom': make_scorer(spcc, greater_is_better=True)
         }

j_arr = []
for j in range (73):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
                     
                    print(clf) 
                    pipe = Pipeline([
                        ('scale', preprocessing.RobustScaler()),
                        ('kbest',SelectKBest(f_regression, k=(j+1))),
                        ('clf2',clf  )])

                    scores = cross_validate(pipe, X, y, scoring=scoring,
                                             cv=tss ,n_jobs=-1, return_train_score=True,verbose=10)
                    
                    print('Correlation = ' + str(scores['test_custom'].mean()))
                    print('Max Error = ' + str(abs(scores['test_max'].mean())))
                    print('Test MAE = ' + str(abs(scores['test_mae'].mean()))) 
                    print('Test RMSE = ' + str(sqrt(abs(scores['test_mse'].mean()))))
                    corr_arr[i] =  scores['test_custom'].mean()
                    mae_arr[i] =  abs(scores['test_mae'].mean())
                    rmse_arr[i] = sqrt(abs(scores['test_mse'].mean()))
                    max_arr[i] = abs(scores['test_max'].mean())
                    i= i+1
                    print('_______________________________________________________________________________')
    j_arr.append(j+1)
    recording['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

train_df Shape: (1097, 47)
After encoding: (1097, 74)
Keeping k-best features where k =  1
StackingCVRegressor(meta_regressor=Ridge(), random_state=42,
                    regressors=(LinearRegression(), Ridge(),
                                ExtraTreesRegressor(n_estimators=1000,
                                                    random_state=0),
                                KNeighborsRegressor(n_neighbors=7),
                                MLPRegressor(alpha=1e-05,
                                             hidden_layer_sizes=(5, 5, 5, 5, 5),
                                             random_state=42, solver='lbfgs')),
                    use_features_in_secondary=True)


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:   21.6s remaining:   21.6s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   25.8s remaining:   11.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   37.9s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0869s.) Setting batch_size=4.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.2s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.1s remaining:    0.1s


Correlation = 0.7120088310515419
Max Error = 1266.6723648441643
Test MAE = 228.6336689503199
Test RMSE = 328.8911002386693
_______________________________________________________________________________
VotingRegressor(estimators=[('gb',
                             GradientBoostingRegressor(n_estimators=10,
                                                       random_state=1)),
                            ('rf',
                             RandomForestRegressor(n_estimators=10,
                                                   random_state=1)),
                            ('lr', LinearRegression()),
                            ('dt',
                             DecisionTreeRegressor(criterion='mae',
                                                   random_state=0)),
                            ('sgd', SGDRegressor())])


[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.3s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0290s.) Setting batch_size=12.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0330s.) Setting batch_size=12.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.0s remaining:    0.0s


Correlation = 0.48955412915716295
Max Error = 1272.7047189510117
Test MAE = 252.13275773418914
Test RMSE = 368.2410470998067
_______________________________________________________________________________
LinearSVR()
Correlation = 0.7206425675623664
Max Error = 1539.3690780945503
Test MAE = 551.2736071921556
Test RMSE = 648.3588871509634
_______________________________________________________________________________
SGDRegressor()


...

[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    9.6s remaining:    9.6s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   10.6s remaining:    4.5s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   15.2s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Correlation = 0.6519917712472875
Max Error = 1171.7183006591797
Test MAE = 234.88642960920234
Test RMSE = 333.7736050926303
_______________________________________________________________________________
LGBMRegressor(learning_rate=0.05, n_estimators=1000)


[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    4.1s remaining:    4.1s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    7.6s remaining:    3.2s


Correlation = 0.6308605542466751
Max Error = 1199.9786320597664
Test MAE = 248.0233444305427
Test RMSE = 338.026146962819
_______________________________________________________________________________
COMPLETE


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   11.0s finished


In [5]:
hotdata

Year  Day  January  February  March  April  May  June  July  August  \
0     2016   25        0         0      0      0    0     0     0       0   
1     2016   26        0         0      0      0    0     0     0       0   
2     2016   27        0         0      0      0    0     0     0       0   
3     2016   28        0         0      0      0    0     0     0       0   
4     2016   29        0         0      0      0    0     0     0       0   
...    ...  ...      ...       ...    ...    ...  ...   ...   ...     ...   
1092  2019    1        0         0      0      0    0     0     0       0   
1093  2019    2        0         0      0      0    0     0     0       0   
1094  2019    3        0         0      0      0    0     0     0       0   
1095  2019    4        0         0      0      0    0     0     0       0   
1096  2019    5        0         0      0      0    0     0     0       0   

      September  October  November  December  Sunday  Monday  Tuesday  \
0             1        0         0         0       1       0        0   
1             1        0         0         0       0       1        0   
2             1        0         0         0       0       0        1   
3             1        0         0         0       0       0        0   
4             1        0         0         0       0       0        0   
...         ...      ...       ...       ...     ...     ...      ...   
1092          0        0         0         1       1       0        0   
1093          0        0         0         1       0       1        0   
1094          0        0         0         1       0       0        1   
1095          0        0         0         1       0       0        0   
1096          0        0         0         1       0       0        0   

      Wednesday  Thursday  Friday  Saturday  Carnival  LentFasting  Ramadan  \
0             0         0       0         0         0            0        0   
1             0         0       0         0         0            0        0   
2             0         0       0         0         0            0        0   
3             1         0       0         0         0            0        0   
4             0         1       0         0         0            0        0   
...         ...       ...     ...       ...       ...          ...      ...   
1092          0         0       0         0         0            0        0   
1093          0         0       0         0         0            0        0   
1094          0         0       0         0         0            0        0   
1095          1         0       0         0         0            0        0   
1096          0         1       0         0         0            0        0   

      ChristmasSeason         0         1         2         3         4  \
0                   0  666.4500  475.4900  320.5400  365.6100  494.9900   
1                   0  475.4900  320.5400  365.6100  494.9900  540.9300   
2                   0  320.5400  365.6100  494.9900  540.9300  862.0400   
3                   0  365.6100  494.9900  540.9300  862.0400  942.9400   
4                   0  494.9900  540.9300  862.0400  942.9400  427.5500   
...               ...       ...       ...       ...       ...       ...   
1092                1 1538.6000  625.7500  659.2400  626.9200  733.8000   
1093                1  625.7500  659.2400  626.9200  733.8000 1219.9700   
1094                1  659.2400  626.9200  733.8000 1219.9700 1971.2400   
1095                1  626.9200  733.8000 1219.9700 1971.2400 1522.0500   
1096                1  733.8000 1219.9700 1971.2400 1522.0500  879.3600   

             5         6         7         8         9        10        11  \
0     540.9300  862.0400  942.9400  427.5500  378.3600  420.9800  541.1600   
1     862.0400  942.9400  427.5500  378.3600  420.9800  541.1600  574.2900   
2     942.9400  427.5500  378.3600  420.9800  541.1600  574.2900  824.2100   
3     427.5500  378.3600  420.9800  541.16

In [6]:
recording

Model      Run0      Run1  \
0   StackingCVRegressor(meta_regressor=Ridge(), ra...  228.6337  215.0625   
1   VotingRegressor(estimators=[('gb',\n          ...  252.1328  244.7921   
2                                         LinearSVR()  551.2736  506.3959   
3                                      SGDRegressor()  222.7321  213.4934   
4   MLPRegressor(alpha=1e-05, hidden_layer_sizes=(...  225.8701  221.3732   
5                                               SVR()  344.7852  345.8205   
6                                             NuSVR()  337.0527  338.6086   
7                                     BayesianRidge()  222.6735  212.0337   
8   DecisionTreeRegressor(criterion='mae', random_...  331.3866  359.0498   
9   ElasticNetCV(cv=10, max_iter=100000, random_st...  239.8593  233.8460   
10                                 LinearRegression()  222.4907  211.2588   
11                                            Ridge()  222.7312  212.0954   
12                                      KernelRidge()  624.1003  646.3885   
13                      LassoCV(cv=5, random_state=0)  222.6529  219.3996   
14                         GaussianProcessRegressor() 1048.6429 7287.2700   
15  ExtraTreesRegressor(n_estimators=1000, random_...  311.5759  254.6660   
16                 KNeighborsRegressor(n_neighbors=7)  239.3096  217.5385   
17  XGBRegressor(base_score=None, booster=None, co...  324.0335  318.1832   
18  LGBMRegressor(learning_rate=0.05, n_estimators...  230.3547  244.0652   

         Run2       Run3       Run4       Run5       Run6           Run7  \
0    214.3644   225.4426   225.6001   237.4540   224.4137       224.4868   
1    246.2745   233.0371   231.9773   238.5780   243.3486  83614127.7558   
2    469.9699   429.1450   421.5869   413.5509   400.0133       422.2367   
3    211.4309   219.5145   223.2598   222.0121   226.8705 282356656.3104   
4    241.8595   239.6267   337.6506   295.0928   299.3661       259.9630   
5    347.5703   347.3481   348.7696   351.2893   352.8251       354.6895   
6    339.4707   339.7390   341.0429   342.6843   343.8966       344.7784   
7    209.9885   219.8727   221.0086   220.3044   220.2829       218.1697   
8    366.2669   340.5136   332.2386   346.7227   388.2628       379.9084   
9    223.9978   232.5397   234.7155   233.8449   232.6957       235.6243   
10   208.8630   219.2362   220.3782   218.9534   219.4704       220.4276   
11   209.5028   219.4545   220.5857   219.2985   219.4059       219.3017   
12   651.0364   545.5289   520.4529   514.3156   497.4007       533.5060   
13   215.4440   222.7971   226.3556   225.5758   223.4199       218.7301   
14 50180.5601 89030.3540 62907.7579 31639.6057 12278.7083      1640.8939   
15   241.0085   247.7091   241.4441   239.1775   240.2416       243.1795   
16   221.5163   226.3903   226.6717   226.2623   228.5580       237.5009   
17   278.0859   271.2577   261.2679   262.7396   267.0230       275.3945   
18   246.1142   252.4295   250.5100   263.0899   272.1003       270.8539   

             Run8           Run9          Run10          Run11  \
0        220.6944       217.8543       228.9792       218.5558   
1  346846026.0268  49177772.7153   4600120.7315 309982215.6256   
2        415.2171       409.3105       402.5517       408.5284   
3  293217835.8430 124365944.3390 651874659.8374 103368209.7432   
4        257.1806       272.5544       272.2375       268.1055   
5        354.9914       355.3796       355.4974       356.4155   
6        344.9064       345.4556       345.7121       346.4701   
7        217.1865       213.7959       213.4747       210.9987   
8        364.6892       381.8762       355.7305       354.3089   
9        233.7954       233.3794       232.5343       232.9689   
10       220.5341       216.4919       216.2729       213.5672   
11       218.6388       214.7905       214.3678       211.7657   
12       499.0646       468.9659       460.4939       474.8420   
13       220.5694       219.4401       219.1904       218.1819

In [7]:
recording.to_csv('ScikitResultsActual02012021.csv')

## Single Day Forecasting - Predict Difference

#### Train and test difference prediction

In [8]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'WeeklyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'DailyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)

diff_add_lookback(data, lookback, df,'DailyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'DailyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

train_df Shape: (1111, 37)
After encoding: (1090, 78)


In [9]:
hotdata

Year  Day  January  February  March  April  May  June  July  August  \
0     2016    2        0         0      0      0    0     0     0       0   
1     2016    3        0         0      0      0    0     0     0       0   
2     2016    4        0         0      0      0    0     0     0       0   
3     2016    5        0         0      0      0    0     0     0       0   
4     2016    6        0         0      0      0    0     0     0       0   
...    ...  ...      ...       ...    ...    ...  ...   ...   ...     ...   
1085  2019    1        0         0      0      0    0     0     0       0   
1086  2019    2        0         0      0      0    0     0     0       0   
1087  2019    3        0         0      0      0    0     0     0       0   
1088  2019    4        0         0      0      0    0     0     0       0   
1089  2019    5        0         0      0      0    0     0     0       0   

      September  October  November  December  Sunday  Monday  Tuesday  \
0             0        1         0         0       1       0        0   
1             0        1         0         0       0       1        0   
2             0        1         0         0       0       0        1   
3             0        1         0         0       0       0        0   
4             0        1         0         0       0       0        0   
...         ...      ...       ...       ...     ...     ...      ...   
1085          0        0         0         1       1       0        0   
1086          0        0         0         1       0       1        0   
1087          0        0         0         1       0       0        1   
1088          0        0         0         1       0       0        0   
1089          0        0         0         1       0       0        0   

      Wednesday  Thursday  Friday  Saturday  Carnival  LentFasting  Ramadan  \
0             0         0       0         0         0            0        0   
1             0         0       0         0         0            0        0   
2             0         0       0         0         0            0        0   
3             1         0       0         0         0            0        0   
4             0         1       0         0         0            0        0   
...         ...       ...     ...       ...       ...          ...      ...   
1085          0         0       0         0         0            0        0   
1086          0         0       0         0         0            0        0   
1087          0         0       0         0         0            0        0   
1088          1         0       0         0         0            0        0   
1089          0         1       0         0         0            0        0   

      ChristmasSeason         0         1        2         3         4  \
0                   0   80.9000 -515.3900 -49.1900   42.6200  120.1800   
1                   0 -515.3900  -49.1900  42.6200  120.1800   33.1300   
2                   0  -49.1900   42.6200 120.1800   33.1300  249.9200   
3                   0   42.6200  120.1800  33.1300  249.9200   60.2900   
4                   0  120.1800   33.1300 249.9200   60.2900 -487.0100   
...               ...       ...       ...      ...       ...       ...   
1085                1 -256.0100 -912.8500  33.4900  -32.3200  106.8800   
1086                1 -912.8500   33.4900 -32.3200  106.8800  486.1700   
1087                1   33.4900  -32.3200 106.8800  486.1700  751.2700   
1088                1  -32.3200  106.8800 486.1700  751.2700 -449.1900   
1089                1  106.8800  486.1700 751.2700 -449.1900 -642.6900   

             5         6          7          8          9         10  \
0      33.1300  249.9200    60.2900  -487.0100   102.0800   -66.0100   
1     249.9200   60.2900  -487.0100   102.0800   -66.0100   -91.1900   
2      60.2900 -487.0100   102.0800   -66.0100   -91.1900   223.6200   
3    -487.0100  102.0800   -66.0100   -91.1900   223.6200   494.1200   
4     

In [10]:

sys.stdout.flush()

clflist=[stack,LR, VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,
         kridge,Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  

recording_diff = pd.DataFrame(clflist,columns=['Model'])


#
scoring = {
    'max' : 'max_error',
    'mae': 'neg_mean_absolute_error',
    'mse' : 'neg_mean_squared_error',
           'custom': make_scorer(spcc, greater_is_better=True)
         }

j_arr = []
for j in range (77):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
                     
                    print(clf) 
                    pipe = Pipeline([
                        ('scale', preprocessing.RobustScaler()),
                        ('kbest',SelectKBest(f_regression, k=(j+1))),
                        ('clf2',clf  )])

                    scores = cross_validate(pipe, X, y, scoring=scoring,
                                             cv=tss ,n_jobs=-1, return_train_score=True,verbose=10)
                    
                    print('Correlation = ' + str(scores['test_custom'].mean()))
                    print('Max Error = ' + str(abs(scores['test_max'].mean())))
                    print('Test MAE = ' + str(abs(scores['test_mae'].mean()))) 
                    print('Test RMSE = ' + str(sqrt(abs(scores['test_mse'].mean()))))
                    corr_arr[i] =  scores['test_custom'].mean()
                    mae_arr[i] =  abs(scores['test_mae'].mean())
                    rmse_arr[i] = sqrt(abs(scores['test_mse'].mean()))
                    max_arr[i] = abs(scores['test_max'].mean())
                    i= i+1
                    print('_______________________________________________________________________________')
    j_arr.append(j+1)
    recording_diff['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

Keeping k-best features where k =  1
StackingCVRegressor(meta_regressor=Ridge(), random_state=42,
                    regressors=(LinearRegression(), Ridge(),
                                ExtraTreesRegressor(n_estimators=1000,
                                                    random_state=0),
                                KNeighborsRegressor(n_neighbors=7),
                                MLPRegressor(alpha=1e-05,
                                             hidden_layer_sizes=(5, 5, 5, 5, 5),
                                             random_state=42, solver='lbfgs')),
                    use_features_in_secondary=True)


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:   13.6s remaining:   13.6s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   15.3s remaining:    6.5s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   21.3s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0330s.) Setting batch_size=12.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Correlation = 0.553999465432707
Max Error = 1319.5699692137143
Test MAE = 336.60240626294376
Test RMSE = 457.6932214672896
_______________________________________________________________________________
LinearRegression()
Correlation = 0.5729629233029895
Max Error = 1329.2348087649207
Test MAE = 316.5186725623045
Test RMSE = 434.86178678601584
_______________________________________________________________________________
VotingRegressor(estimators=[('gb',
                             GradientBoostingRegressor(n_estimators=10,
                                                       random_state=1)),
                            ('rf',
                             RandomForestRegressor(n_estimators=10,
                                                   random_state=1)),
                            ('lr', LinearRegression()),
                            ('dt',
                             DecisionTreeRegressor(criterion='mae',
                                                   random_state

[Parallel(n_jobs=-1)]: Batch computation too fast (0.0859s.) Setting batch_size=4.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.1s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.1s remaining:    0.1s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.2s finished


Correlation = 0.4914226332942239
Max Error = 1375.9685570227846
Test MAE = 319.9745826699809
Test RMSE = 440.3894271719601
_______________________________________________________________________________
LinearSVR()
Correlation = 0.5729629233029895
Max Error = 1392.8245233932532
Test MAE = 362.69993065082235
Test RMSE = 496.6247987860856
_______________________________________________________________________________
SGDRegressor()


...

[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:   10.2s remaining:   10.2s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   10.9s remaining:    4.6s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   15.8s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Correlation = 0.7284256829861666
Max Error = 1073.4972163124085
Test MAE = 257.233420360169
Test RMSE = 343.39504052642263
_______________________________________________________________________________
LGBMRegressor(learning_rate=0.05, n_estimators=1000)


[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    4.2s remaining:    4.2s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    8.4s remaining:    3.6s


Correlation = 0.7221178218733992
Max Error = 1124.1877366422773
Test MAE = 258.4031250446213
Test RMSE = 347.1867726771838
_______________________________________________________________________________
COMPLETE


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   12.2s finished


In [11]:
recording_diff

Model     Run0     Run1  \
0   StackingCVRegressor(meta_regressor=Ridge(), ra... 336.6024 304.6264   
1                                  LinearRegression() 316.5187 297.5148   
2   VotingRegressor(estimators=[('gb',\n          ... 319.9746 312.0231   
3                                         LinearSVR() 362.6999 337.9587   
4                                      SGDRegressor() 316.9346 298.4244   
5   MLPRegressor(alpha=1e-05, hidden_layer_sizes=(... 315.9653 329.2873   
6                                               SVR() 355.7065 362.0608   
7                                             NuSVR() 357.7625 363.0588   
8                                     BayesianRidge() 316.7680 298.2784   
9   DecisionTreeRegressor(criterion='mae', random_... 331.5666 390.9711   
10  ElasticNetCV(cv=10, max_iter=100000, random_st... 332.9715 324.3670   
11                                 LinearRegression() 316.5187 297.5148   
12                                            Ridge() 316.9568 297.9552   
13                                      KernelRidge() 324.7700 304.6952   
14                      LassoCV(cv=5, random_state=0) 318.2747 318.0856   
15                         GaussianProcessRegressor() 315.0739 621.5061   
16  ExtraTreesRegressor(n_estimators=1000, random_... 326.4308 361.0565   
17                 KNeighborsRegressor(n_neighbors=7) 333.8767 311.6216   
18  XGBRegressor(base_score=None, booster=None, co... 333.1667 371.0381   
19  LGBMRegressor(learning_rate=0.05, n_estimators... 317.5880 321.6185   

        Run2       Run3       Run4       Run5       Run6      Run7     Run8  \
0   291.1486   284.5089   266.3447   256.9018   248.4459  252.3653 248.7524   
1   284.8755   279.9968   278.2352   277.8660   276.1626  276.5802 274.2237   
2   294.1223   280.5621   267.9438   267.7220   268.8841  268.1392 263.5619   
3   332.3260   325.8524   320.1627   315.5295   313.2400  309.0200 304.9974   
4   285.8056   281.1177   280.7302   280.4602   278.4446  277.8988 274.6969   
5   285.4693   307.1509   281.6017   278.8951   281.7656  302.6410 266.5516   
6   362.3459   363.5519   361.5769   361.9499   362.2582  362.8714 363.8167   
7   363.3301   364.3709   362.6563   363.0597   363.2914  364.0109 364.8784   
8   286.0271   280.9752   279.4840   279.2309   277.2937  277.1481 274.1644   
9   361.4883   354.2619   319.6700   351.1604   372.1870  370.8108 351.1146   
10  316.5218   314.6972   318.2212   314.0833   309.2370  302.3669 292.9253   
11  284.8755   279.9968   278.2352   277.8660   276.1626  276.5802 274.2237   
12  285.3112   280.3592   278.4963   278.1213   276.3296  276.5588 273.9604   
13  288.0879   282.2445   280.1438   278.6443   275.7905  276.1160 275.2532   
14  308.5765   319.9746   349.1692   349.1692   341.9346  342.0956 324.0002   
15 8266.4415 52231.5469 57268.8186 61387.5360 12143.7228 1225.0735 475.5728   
16  331.4641   296.9630   263.6487   263.8790   253.2507  248.5719 247.3531   
17  293.4506   289.5335   275.7418   274.9216   271.5714  275.1802 277.1237   
18  344.4278   320.6681   283.0942   295.0858   281.2994  271.2931 272.0571   
19  308.6615   315.8838   293.7962   286.0076   277.2948  281.8692 274.4068   

       Run9    Run10    Run11    Run12    Run13    Run14    Run15    Run16  \
0  247.7180 249.6306 249.8971 247.3509 243.9066 245.1163 244.2662 247.6681   
1  273.5025 274.7582 267.9363 267.8729 264.2766 264.4226 265.8036 265.6544   
2  261.5829 259.5249 254.8463 254.3503 250.7655 253.4588 251.8244 253.8204   
3  304.7117 303.9431 297.1147 296.9171 296.7149 296.5257 295.8651 295.3363   
4  275.1953 276.7788 269.6091 270.2507 267.6379 267.3901 267.5323 268.7113   
5  300.2595 280.9609 333.5958 307.5567 291.1863 287.5684 306.8193 280.2385   
6  364.3146 364.7947 364.7632 364.8212 364.8686 364.9405 365.0902 365.1631   
7  365.3787 365.8712 365.8624 365.8940 365.9305 366.0163 366.1105 366.1500   
8  274.0162 275.1265 268.6303 268.0428 265.2736 265.6620 264.8231 265.2092   
9  340.2830 335.7346 330.8585 32

In [12]:
recording_diff.to_csv('ScikitResultsDailyDiff02012021.csv')

## Weekly Difference 

In [13]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'DailyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'WeeklyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

diff_add_lookback(data, lookback, df,'WeeklyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'WeeklyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

train_df Shape: (1111, 37)
After encoding: (1090, 78)


In [14]:

sys.stdout.flush()

clflist=[stack,LR, VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,
         kridge,Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  

recording_diff = pd.DataFrame(clflist,columns=['Model'])


#
scoring = {
    'max' : 'max_error',
    'mae': 'neg_mean_absolute_error',
    'mse' : 'neg_mean_squared_error',
           'custom': make_scorer(spcc, greater_is_better=True)
         }

j_arr = []
for j in range (77):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
                     
                    print(clf) 
                    pipe = Pipeline([
                        ('scale', preprocessing.RobustScaler()),
                        ('kbest',SelectKBest(f_regression, k=(j+1))),
                        ('clf2',clf  )])

                    scores = cross_validate(pipe, X, y, scoring=scoring,
                                             cv=tss ,n_jobs=-1, return_train_score=True,verbose=10)
                    
                    print('Correlation = ' + str(scores['test_custom'].mean()))
                    print('Max Error = ' + str(abs(scores['test_max'].mean())))
                    print('Test MAE = ' + str(abs(scores['test_mae'].mean()))) 
                    print('Test RMSE = ' + str(sqrt(abs(scores['test_mse'].mean()))))
                    corr_arr[i] =  scores['test_custom'].mean()
                    mae_arr[i] =  abs(scores['test_mae'].mean())
                    rmse_arr[i] = sqrt(abs(scores['test_mse'].mean()))
                    max_arr[i] = abs(scores['test_max'].mean())
                    i= i+1
                    print('_______________________________________________________________________________')
    j_arr.append(j+1)
    recording_diff['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

Keeping k-best features where k =  1
StackingCVRegressor(meta_regressor=Ridge(), random_state=42,
                    regressors=(LinearRegression(), Ridge(),
                                ExtraTreesRegressor(n_estimators=1000,
                                                    random_state=0),
                                KNeighborsRegressor(n_neighbors=7),
                                MLPRegressor(alpha=1e-05,
                                             hidden_layer_sizes=(5, 5, 5, 5, 5),
                                             random_state=42, solver='lbfgs')),
                    use_features_in_secondary=True)


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:   17.7s remaining:   17.7s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   22.4s remaining:    9.5s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   35.4s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0310s.) Setting batch_size=12.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Correlation = nan
Max Error = 1381.1287459944585
Test MAE = 237.77401309450488
Test RMSE = 344.69213560454506
_______________________________________________________________________________
LinearRegression()
Correlation = nan
Max Error = 1361.459637298019
Test MAE = 236.02727268544658
Test RMSE = 343.3654324279687
_______________________________________________________________________________
VotingRegressor(estimators=[('gb',
                             GradientBoostingRegressor(n_estimators=10,
                                                       random_state=1)),
                            ('rf',
                             RandomForestRegressor(n_estimators=10,
                                                   random_state=1)),
                            ('lr', LinearRegression()),
                            ('dt',
                             DecisionTreeRegressor(criterion='mae',
                                                   random_state=0)),
                       

[Parallel(n_jobs=-1)]: Batch computation too fast (0.0929s.) Setting batch_size=4.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.2s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.1s remaining:    0.1s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.3s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.0280s.) Setting batch_size=14.
[Parallel(n_jobs=-1)]: Done   3 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:    0.0s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
[Parallel(n_jobs=-1)]: Batch computation too fast (0.

Correlation = nan
Max Error = 1404.188287576351
Test MAE = 250.44269475690203
Test RMSE = 361.20062891662764
_______________________________________________________________________________
LinearSVR()
Correlation = nan
Max Error = 1404.5947564757591
Test MAE = 240.09732683298813
Test RMSE = 348.0564237143471
_______________________________________________________________________________
SGDRegressor()


...

[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:   12.7s remaining:   12.7s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   14.0s remaining:    5.9s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   21.9s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.


Correlation = 0.46285140634972227
Max Error = 1239.8044414978026
Test MAE = 247.82314071417335
Test RMSE = 342.3409008288997
_______________________________________________________________________________
LGBMRegressor(learning_rate=0.05, n_estimators=1000)


[Parallel(n_jobs=-1)]: Done   5 out of  10 | elapsed:    6.7s remaining:    6.7s
[Parallel(n_jobs=-1)]: Done   7 out of  10 | elapsed:   11.8s remaining:    5.0s


Correlation = 0.40282340346267886
Max Error = 1341.7442057680869
Test MAE = 255.0737886023001
Test RMSE = 354.849361456239
_______________________________________________________________________________
COMPLETE


[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:   16.4s finished


In [15]:
recording_diff

Model       Run0       Run1  \
0   StackingCVRegressor(meta_regressor=Ridge(), ra...   237.7740   236.5938   
1                                  LinearRegression()   236.0273   233.9576   
2   VotingRegressor(estimators=[('gb',\n          ...   250.4427   250.9236   
3                                         LinearSVR()   240.0973   239.4826   
4                                      SGDRegressor()   236.1603   235.2342   
5   MLPRegressor(alpha=1e-05, hidden_layer_sizes=(...   238.0694   235.5436   
6                                               SVR()   248.4208   248.8830   
7                                             NuSVR()   249.0839   249.5688   
8                                     BayesianRidge()   236.0825   234.0953   
9   DecisionTreeRegressor(criterion='mae', random_...   322.0390   335.3159   
10  ElasticNetCV(cv=10, max_iter=100000, random_st...   236.4421   236.1793   
11                                 LinearRegression()   236.0273   233.9576   
12                                            Ridge()   236.0311   234.3735   
13                                      KernelRidge()   235.6828   233.6550   
14                      LassoCV(cv=5, random_state=0)   236.3147   235.4090   
15                         GaussianProcessRegressor() 20424.2219 22875.7392   
16  ExtraTreesRegressor(n_estimators=1000, random_...   298.8988   288.5443   
17                 KNeighborsRegressor(n_neighbors=7)   253.8049   247.8859   
18  XGBRegressor(base_score=None, booster=None, co...   310.8678   298.9236   
19  LGBMRegressor(learning_rate=0.05, n_estimators...   256.1669   259.7002   

         Run2       Run3       Run4       Run5       Run6       Run7  \
0    237.4740   236.5801   239.6020   235.1706   236.5812   237.2352   
1    233.2992   229.0895   230.4321   230.7307   231.1690   230.0887   
2    245.2359   237.6390   237.0813   234.9812   236.4608   235.9564   
3    238.9544   237.3948   237.4793   237.2642   236.9395   236.0589   
4    235.3719   233.8562   234.8894   235.1229   236.4821   234.4766   
5    237.0838   235.3928   261.9263   242.4082   233.5832   241.3669   
6    249.8041   249.6296   249.7809   249.8169   250.2997   250.5893   
7    250.6312   250.5562   250.6655   250.6792   251.1148   251.4510   
8    233.3013   229.2588   230.7264   230.9764   231.6329   230.5943   
9    339.1071   324.0316   320.6813   312.8821   315.2490   307.2389   
10   235.8998   233.5711   234.5550   233.3322   234.4145   233.1202   
11   233.2992   229.0895   230.4321   230.7307   231.1690   230.0887   
12   233.5085   230.1129   231.8763   231.8031   232.6645   231.5303   
13   233.0469   229.1690   230.3787   230.1287   231.0054   229.9956   
14   235.5000   233.3741   234.5113   234.3949   234.1285   230.2316   
15 29637.3206 38365.3297 36988.4986 36174.3234 42444.6100 50282.2295   
16   266.7137   251.8445   254.3761   252.1760   248.8852   246.4084   
17   242.2932   240.4833   240.0714   239.8375   237.5985   239.0672   
18   287.6629   273.3628   273.4590   269.4478   264.7187   262.1801   
19   265.1654   264.9149   267.7605   268.3370   264.9589   264.3655   

         Run8       Run9      Run10      Run11      Run12     Run13  \
0    234.5432   232.7827   232.9461   232.0938   232.9117  227.5918   
1    228.1224   226.3778   225.8171   226.2357   226.5331  225.5843   
2    234.3509   232.9937   231.0855   229.5143   230.6137  230.6299   
3    235.8544   235.6858   236.0835   235.9507   235.9410  234.8982   
4    233.7243   233.7271   233.7846   234.4437   234.5428  233.1818   
5    238.6512   241.3511   248.4668   245.3196   252.0514  266.2695   
6    250.6344   250.9197   251.2842   251.4682   251.6882  251.9372   
7    251.5071   251.7108   252.0505   252.2128   252.4422  252.6279   
8    228.6908   227.0877   226.6388   227.2612   227.5813  226.3056   
9    301.0352   312.9614   307.6201   302.9527   307.6947  323.5271   
10   232.4308   232.3412   233.2276   233.3389   233.5306  231.8210   
11   228.1224   226.377

In [16]:
recording_diff.to_csv('ScikitResultsWeeklyDiff02012021.csv')

## Full Week Forecasting - Predicted in One Shot

In [ ]:
from sklearn.multioutput import MultiOutputRegressor
from sklearn.neural_network import MLPRegressor
nn = MultiOutputRegressor( MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42) )
stack_nn =  MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42)
from sklearn.neighbors import KNeighborsRegressor
neigh = MultiOutputRegressor(KNeighborsRegressor(n_neighbors=7))
stack_neigh = KNeighborsRegressor(n_neighbors=7)

from mlxtend.regressor import StackingCVRegressor
from sklearn.multioutput import MultiOutputRegressor
from sklearn.linear_model import Ridge
LR = LinearRegression()
rid = Ridge(alpha=1.0)
et = ExtraTreesRegressor(n_estimators=1000, random_state=0)

stack = MultiOutputRegressor(StackingCVRegressor(regressors=(LR, rid, et, stack_neigh, stack_nn),
                            meta_regressor=rid, 
                            random_state=42,
                            use_features_in_secondary=True))




lgbm = MultiOutputRegressor(lgb.LGBMRegressor(num_leaves=31,
                        learning_rate=0.05,
                        n_estimators=1000,n_jobs=-1))

XGBModel = MultiOutputRegressor(XGBRegressor(learning_rate =0.05,
 n_estimators=2000,
 max_depth=5,
 min_child_weight=1,
 gamma=0.1,
 subsample=0.8,
 colsample_bytree=0.8,
 objective= 'reg:squarederror',
 nthread=5,
 scale_pos_weight=1,
 seed=21,
 eval_metric = ['mae']))

ETCModel  = MultiOutputRegressor(ExtraTreesRegressor(n_estimators=1000, random_state=0))

from sklearn.gaussian_process import GaussianProcessRegressor
gpr = MultiOutputRegressor(GaussianProcessRegressor())

from sklearn.linear_model import SGDRegressor
from sklearn.linear_model import LassoCV
Lcv = MultiOutputRegressor(LassoCV(cv=5, random_state=0))
LR = MultiOutputRegressor(LinearRegression())
SGD = MultiOutputRegressor(SGDRegressor(max_iter=1000, tol=1e-3))



from sklearn.linear_model import Ridge
ridge = MultiOutputRegressor(Ridge(alpha=1.0))

from sklearn.linear_model import ElasticNetCV
els = MultiOutputRegressor(ElasticNetCV(cv=10, random_state=0,max_iter=100000) )  

from sklearn.tree import DecisionTreeRegressor   
dt = MultiOutputRegressor(DecisionTreeRegressor(random_state=0,criterion="mae") )

from sklearn.kernel_ridge import KernelRidge
kridge = MultiOutputRegressor(KernelRidge())

from sklearn.linear_model import BayesianRidge
bridge = MultiOutputRegressor(BayesianRidge())

from sklearn.svm import SVR, NuSVR, LinearSVR
svr = MultiOutputRegressor(SVR())
nusvr = MultiOutputRegressor(NuSVR())
linsvr = MultiOutputRegressor(LinearSVR())

from sklearn.ensemble import GradientBoostingRegressor
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import VotingRegressor
from sklearn.linear_model import SGDRegressor

reg1 = GradientBoostingRegressor(random_state=1, n_estimators=10)
reg2 = RandomForestRegressor(random_state=1, n_estimators=10)
reg3 = LinearRegression()
reg4 = DecisionTreeRegressor(random_state=0,criterion="mae")
reg5 = SGDRegressor(max_iter=1000, tol=1e-3)

VR = MultiOutputRegressor(
    VotingRegressor(estimators=[('gb', reg1), ('rf', reg2), ('lr', reg3), ('dt',reg4), ('sgd',reg5)]))

from sklearn.neural_network import MLPRegressor
nn = MultiOutputRegressor( MLPRegressor(solver='lbfgs', alpha=1e-5,
                     hidden_layer_sizes=(5, 5, 5, 5, 5), random_state=42) )

tss = TimeSeriesSplit(n_splits = 10)

### Actual Test

In [5]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','DailyAvg','DailyBusyness'])

lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason',
                         'WeeklyAvg','MinSales','MaxSales',
                         'WeeklyBusyness',
                         0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                          14, 15, 16, 17, 18, 19,      
                         '2to5']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

lb_data = add_lookback(data, lookback, df)
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholiday(lb_data)
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])

hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]

scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[stack,LR,VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,kridge, 
         Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  
#,
recording = pd.DataFrame(clflist,columns=['Model'])

scoring = {
        'mae': 'neg_mean_absolute_error',
        'mse' : 'neg_mean_squared_error',
        'custom': make_scorer(spcc, greater_is_better=True)
    }

j_arr = []
for j in range (71):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
            feat_reduction = SelectKBest(f_regression, k=j+1) 
            X_new = feat_reduction.fit_transform(X,y[:,0])
            print(clf) 
            X_train, X_test, y_train, y_test = train_test_split(X_new, y, test_size=221, random_state=42, shuffle=False)

            clf.fit(X_train, y_train)
            y_pred = clf.predict(X_test)
            
            meansq = keras.metrics.mean_squared_error(y_test.flatten(), y_pred.flatten()).numpy()
            meanabs = keras.metrics.mean_absolute_error(y_test.flatten(), y_pred.flatten()).numpy()
            print("MSE = "+str(meansq))
            print("MAE = "+str(meanabs))
            mae_arr[i]=meanabs
            i= i+1
            print('_______________________________________________________________________________')
    
    j_arr.append(j+1)
    recording['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

train_df Shape: (1091, 51)
After encoding: (1091, 72)
Keeping k-best features where k =  1
KernelRidge()
MSE = 1433212.909728255
MAE = 1093.0960623541816
_______________________________________________________________________________
Keeping k-best features where k =  2
KernelRidge()
MSE = 1389094.1751076484
MAE = 1069.8013849621777
_______________________________________________________________________________
Keeping k-best features where k =  3
KernelRidge()
MSE = 2250755.2643441064
MAE = 1365.9631619982451
_______________________________________________________________________________
Keeping k-best features where k =  4
KernelRidge()
MSE = 1489695.4421887915
MAE = 1072.8163548437626
_______________________________________________________________________________
Keeping k-best features where k =  5
KernelRidge()
MSE = 1339365.1811210543
MAE = 1006.3930930005262
_______________________________________________________________________________
Keeping k-best features where k =  6
Kerne

MSE = 199022.61958152722
MAE = 324.7048001652682
_______________________________________________________________________________
Keeping k-best features where k =  47
KernelRidge()
MSE = 198498.29138840717
MAE = 324.4546275559508
_______________________________________________________________________________
Keeping k-best features where k =  48
KernelRidge()
MSE = 205895.10854682597
MAE = 331.80752440100053
_______________________________________________________________________________
Keeping k-best features where k =  49
KernelRidge()
MSE = 205982.74543103296
MAE = 332.0065504997875
_______________________________________________________________________________
Keeping k-best features where k =  50
KernelRidge()
MSE = 208945.53633574178
MAE = 335.27676668272545
_______________________________________________________________________________
Keeping k-best features where k =  51
KernelRidge()
MSE = 203913.43632889766
MAE = 330.5907925345777
____________________________________________

In [19]:
recording

Model      Run0      Run1  \
0   MultiOutputRegressor(estimator=StackingCVRegre...  359.6526  357.7190   
1   MultiOutputRegressor(estimator=LinearRegressio...  367.1246  366.5583   
2   MultiOutputRegressor(estimator=VotingRegressor...  377.1560  371.6426   
3         MultiOutputRegressor(estimator=LinearSVR())  594.5547  571.6701   
4      MultiOutputRegressor(estimator=SGDRegressor())  367.0418  366.4131   
5   MultiOutputRegressor(estimator=MLPRegressor(al...  356.3621  357.0329   
6               MultiOutputRegressor(estimator=SVR())  409.1775  409.2186   
7             MultiOutputRegressor(estimator=NuSVR())  398.3616  398.3915   
8     MultiOutputRegressor(estimator=BayesianRidge())  366.3965  365.5068   
9   MultiOutputRegressor(estimator=DecisionTreeReg...  501.6786  507.2897   
10  MultiOutputRegressor(estimator=ElasticNetCV(cv...  369.2746  367.0738   
11  MultiOutputRegressor(estimator=LinearRegressio...  367.1246  366.5583   
12            MultiOutputRegressor(estimator=Ridge())  367.1237  366.5545   
13      MultiOutputRegressor(estimator=KernelRidge()) 1093.0961 1069.8014   
14  MultiOutputRegressor(estimator=LassoCV(cv=5, r...  367.0874  366.5521   
15  MultiOutputRegressor(estimator=GaussianProcess...  441.5208 7744.0803   
16  MultiOutputRegressor(estimator=ExtraTreesRegre...  452.6615  398.5342   
17  MultiOutputRegressor(estimator=KNeighborsRegre...  385.0637  376.3497   
18  MultiOutputRegressor(estimator=XGBRegressor(ba...  456.5811  432.2968   
19  MultiOutputRegressor(estimator=LGBMRegressor(l...  394.9362  429.2081   

         Run2       Run3       Run4       Run5      Run6      Run7      Run8  \
0    353.2975   370.1505   323.1348   313.2734  300.2909  294.6096  291.9610   
1    391.7670   390.6449   347.6209   343.3089  330.4358  328.0482  325.4262   
2    365.1865   366.2465   334.5875   331.8230  310.7110  305.3086  307.7173   
3    638.4721   659.6893   634.7763   626.1186  599.9580  586.8412  568.7161   
4    389.6493   389.4105   346.0080   339.8420  325.7006  322.5263  321.3402   
5    372.7454   368.9433   348.3582   323.7061  391.6673  299.0015  315.5116   
6    399.2244   397.2841   397.3578   398.5316  398.0449  398.4912  398.2422   
7    390.1759   388.2690   388.3227   389.7899  389.4430  390.1102  388.2415   
8    390.3978   389.5434   346.7612   341.8490  328.7392  326.1725  322.6641   
9    506.7350   515.5765   457.8255   480.0957  464.7516  449.5900  473.3916   
10   355.6830   364.0888   325.8598   321.0686  305.4733  301.7636  297.4138   
11   391.7670   390.6449   347.6209   343.3089  330.4358  328.0482  325.4262   
12   390.6643   390.0022   346.8086   342.2083  328.8770  326.3935  323.6036   
13  1365.9632  1072.8164  1006.3931  1067.9721  981.9856  954.7584  635.0727   
14   387.7986   386.8337   343.3830   338.5692  324.8024  322.2901  316.3534   
15 33550.9908 80282.1184 76102.4222 56945.7638 8566.2074 1768.2345 1255.5568   
16   391.3741   392.1431   345.3104   338.0195  315.2183  302.2835  302.7676   
17   357.8489   360.6693   308.2479   308.3900  282.7895  278.3082  278.2470   
18   405.4423   410.7141   373.3523   364.0409  345.7656  330.2416  332.0713   
19   404.5815   410.5187   368.6148   367.3416  350.7051  336.8422  338.7896   

       Run9    Run10    Run11    Run12    Run13    Run14    Run15    Run16  \
0  294.8759 290.8315 290.8508 263.5906 269.0284 256.3859 254.4654 252.1048   
1  326.2130 321.4587 317.2174 300.9391 289.4668 285.5259 273.7746 271.5001   
2  304.4920 305.7570 301.1585 276.6531 275.1318 263.4738 253.3475 252.5559   
3  563.1825 563.2489 563.1823 549.6603 546.7661 534.1701 520.9696 524.2530   
4  317.5100 313.1286 307.6731 291.9930 282.8291 279.1055 266.5006 267.2516   
5  297.4971 289.0016 315.7557 303.2731 294.2996 309.0430 283.1638 279.8228   
6  398.7628 398.6368 398.4984 398.3769 398.2759 398.5165 398.6970 398.0352   
7  388.8959 389.0620 389.2242 389.0315 389.1603 389.4725 389.7027 389.5433   
8  322.4538 316.9876 312.7554 296.5686 287.4252

In [20]:
recording.to_csv('ScikitResultsWeek02012021.csv')

### Daily Difference

In [21]:
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['DMY','MissingPrevDays','WeeklyDifference','DiffDifference','2to5'
                                ,'DailyBusyness','DailyAvg','AvgDailyDiff'])

remove=14
df = data.drop([x for x in range(remove)])
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

#df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)
#df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

hotdata = onehotholidaydiff(df,'DailyDifference')

numcols = len(hotdata.columns)
dataset = hotdata
dataset

Index  Group  Year  Day  January  February  March  April  May  June  \
0        15      0  2016   25        0         0      0      0    0     0   
1        16      0  2016   26        0         0      0      0    0     0   
2        17      0  2016   27        0         0      0      0    0     0   
3        18      0  2016   28        0         0      0      0    0     0   
4        19      0  2016   29        0         0      0      0    0     0   
...     ...    ...   ...  ...      ...       ...    ...    ...  ...   ...   
1092   1107      0  2019    1        0         0      0      0    0     0   
1093   1108      0  2019    2        0         0      0      0    0     0   
1094   1109      0  2019    3        0         0      0      0    0     0   
1095   1110      0  2019    4        0         0      0      0    0     0   
1096   1111      0  2019    5        0         0      0      0    0     0   

      July  August  September  October  November  December  Sunday  Monday  \
0        0       0          1        0         0         0       1       0   
1        0       0          1        0         0         0       0       1   
2        0       0          1        0         0         0       0       0   
3        0       0          1        0         0         0       0       0   
4        0       0          1        0         0         0       0       0   
...    ...     ...        ...      ...       ...       ...     ...     ...   
1092     0       0          0        0         0         1       1       0   
1093     0       0          0        0         0         1       0       1   
1094     0       0          0        0         0         1       0       0   
1095     0       0          0        0         0         1       0       0   
1096     0       0          0        0         0         1       0       0   

      Tuesday  Wednesday  Thursday  Friday  Saturday  Carnival  LentFasting  \
0           0          0         0       0         0         0            0   
1           0          0         0       0         0         0            0   
2           1          0         0       0         0         0            0   
3           0          1         0       0         0         0            0   
4           0          0         1       0         0         0            0   
...       ...        ...       ...     ...       ...       ...          ...   
1092        0          0         0       0         0         0            0   
1093        0          0         0       0         0         0            0   
1094        1          0         0       0         0         0            0   
1095        0          1         0       0         0         0            0   
1096        0          0         1       0         0         0            0   

      Ramadan  ChristmasSeason  WeeklyAvg  MinSales  MaxSales  WeeklyBusyness  \
0           0                0   804.6950  320.5400  942.9400          0.7779   
1           0                0   451.5200  320.5400  942.9400          0.2104   
2           0                0   349.4500  320.5400  942.9400          0.0464   
3           0                0   393.2950  320.5400  942.9400          0.1169   
4           0                0   518.0750  320.5400  942.9400          0.3174   
...       ...              ...        ...       ...       ...             ...   
1092        0                1  1445.3206  225.3000 2889.2300          0.4580   
1093        0                1   809.8104  225.3000 2889.2300          0.2194   
1094        0                1   769.9493  225.3000 2889.2300          0.2044   
1095        0                1   839.7848  225.3000 2889.2300          0.2307   
1096        0                1   827.5773  225.3000 2889.2300          0.2261   

      AvgWeeklyDiff  MinDailyDiff  MaxDailyDiff     A0     A1     A2     A3  \
0          276.4900     -515.3900      321.1100 1.0000 0.0000 0.0000 0.0000   
1          -47.9400     -515.3900      321.1100 1.0000 0.0000 0.

In [22]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','DailyAvg','DailyBusyness','AvgDailyDiff'])
remove=14
data = data.drop([x for x in range(remove)])
data = data.reset_index(drop=True)
lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason','WeeklyAvg','MinSales','MaxSales',
                          'WeeklyBusyness','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff',
                                 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                 14, 15, 16, 17, 18, 19,  
                        'DailyDifference']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

#df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)
#df["WeeklyDifference"] = df.WeeklyDifference.astype(float

lb_data = diff_add_lookback(data, lookback, df,'DailyDifference')
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholidaydiff(lb_data, 'DailyDifference')
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])

hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]
X=X.astype(float)
y=y.astype(float)
scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[stack,LR,VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,kridge, 
         Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  
#,
week_daydiff_recording = pd.DataFrame(clflist,columns=['Model'])

scoring = {
        'mae': 'neg_mean_absolute_error',
        'mse' : 'neg_mean_squared_error',
        'custom': make_scorer(spcc, greater_is_better=True)
    }

j_arr = []
for j in range (74):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
            feat_reduction = SelectKBest(f_regression, k=j+1) 
            X_new = feat_reduction.fit_transform(X,y[:,0])
            print(clf) 
            X_train, X_test, y_train, y_test = train_test_split(X_new, y, test_size=221, random_state=42, shuffle=False)

            clf.fit(X_train, y_train)
            y_pred = clf.predict(X_test)
            
            meansq = keras.metrics.mean_squared_error(y_test.flatten(), y_pred.flatten()).numpy()
            meanabs = keras.metrics.mean_absolute_error(y_test.flatten(), y_pred.flatten()).numpy()
            print("MSE = "+str(meansq))
            print("MAE = "+str(meanabs))
            mae_arr[i]=meanabs
            i= i+1
            print('_______________________________________________________________________________')
    
    j_arr.append(j+1)
    week_daydiff_recording['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

train_df Shape: (1077, 54)
After encoding: (1077, 75)
Keeping k-best features where k =  1
MultiOutputRegressor(estimator=StackingCVRegressor(meta_regressor=Ridge(),
                                                   random_state=42,
                                                   regressors=(LinearRegression(),
                                                               Ridge(),
                                                               ExtraTreesRegressor(n_estimators=1000,
                                                                                   random_state=0),
                                                               KNeighborsRegressor(n_neighbors=7),
                                                               MLPRegressor(alpha=1e-05,
                                                                            hidden_layer_sizes=(5,
                                                                                                5,
                       

MSE = 277069.2081541718
MAE = 389.25292761008876
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 278169.99213824363
MAE = 389.14137843778
_______________________________________________________________________________
MultiOutputRegressor(estimator=VotingRegressor(estimators=[('gb',
                                                            GradientBoostingRegressor(n_estimators=10,
                                                                                      random_state=1)),
                                                           ('rf',
                                                            RandomForestRegressor(n_estimators=10,
                                                                                  random_state=1)),
                                                           ('lr',
                                                            LinearRegression()),
        

MSE = 291157.0138086737
MAE = 398.80540041431993
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearSVR())
MSE = 285516.107142717
MAE = 395.33871538976297
_______________________________________________________________________________
MultiOutputRegressor(estimator=SGDRegressor())
MSE = 264431.92287766025
MAE = 375.8764488338491
_______________________________________________________________________________
MultiOutputRegressor(estimator=MLPRegressor(alpha=1e-05,
                                            hidden_layer_sizes=(5, 5, 5, 5, 5),
                                            random_state=42, solver='lbfgs'))
MSE = 269134.76321112877
MAE = 379.24397452000807
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 296587.76785936096
MAE = 402.1128887893912
_______________________________________________________________________________
MultiOutput

MSE = 274094.25318892195
MAE = 385.4405375268383
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 298293.29486898315
MAE = 403.46644124186963
_______________________________________________________________________________
MultiOutputRegressor(estimator=NuSVR())
MSE = 298027.97987045377
MAE = 404.1521139283737
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 265073.7426939401
MAE = 375.7004992183316
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 513321.53745404026
MAE = 546.4874595992244
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                     

MAE = 401.90421217743364
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 244630.86476513627
MAE = 360.90379371512694
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 479041.5356283774
MAE = 521.5536974789916
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                                            random_state=0))
MSE = 257390.5659077861
MAE = 373.47471608544265
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 243461.78235163837
MAE = 359.57925456952574
_______________________________________________________________________________
MultiOutpu

...

MSE = 372319.3994926956
MAE = 462.6889204912735
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                                            random_state=0))
MSE = 189918.8407964759
MAE = 315.1635997025653
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 174477.30684339048
MAE = 291.7787556561085
_______________________________________________________________________________
MultiOutputRegressor(estimator=Ridge())
MSE = 171436.72603842596
MAE = 288.8033454372506
_______________________________________________________________________________
MultiOutputRegressor(estimator=KernelRidge())
MSE = 171260.29730127205
MAE = 288.6808869098209
_______________________________________________________________________________
MultiOutputRegressor(estimator=LassoCV(cv=5, random_state=0))
MSE = 169231.93904707528
MAE 

MSE = 171285.96078131808
MAE = 288.7354419539089
_______________________________________________________________________________
MultiOutputRegressor(estimator=LassoCV(cv=5, random_state=0))
MSE = 169229.71032131644
MAE = 286.7693633420618
_______________________________________________________________________________
MultiOutputRegressor(estimator=GaussianProcessRegressor())
MSE = 285443.70673788205
MAE = 395.15356747440103
_______________________________________________________________________________
MultiOutputRegressor(estimator=ExtraTreesRegressor(n_estimators=1000,
                                                   random_state=0))
MSE = 195550.89405741534
MAE = 318.40467025856503
_______________________________________________________________________________
MultiOutputRegressor(estimator=KNeighborsRegressor(n_neighbors=7))
MSE = 195864.30213327843
MAE = 318.75231969710956
_______________________________________________________________________________
MultiOutputRegressor(estim

MSE = 286852.9686493457
MAE = 396.2898900440611
_______________________________________________________________________________
MultiOutputRegressor(estimator=ExtraTreesRegressor(n_estimators=1000,
                                                   random_state=0))
MSE = 195235.18356506983
MAE = 318.42740003878487
_______________________________________________________________________________
MultiOutputRegressor(estimator=KNeighborsRegressor(n_neighbors=7))
MSE = 194654.3944645331
MAE = 318.79782805429863
_______________________________________________________________________________
MultiOutputRegressor(estimator=XGBRegressor(base_score=None, booster=None,
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=0.8,
                                            eval_metric=['mae'], gamma=0.1,
                                            gpu_id=None,

MSE = 196106.62339088693
MAE = 319.5628220518976
_______________________________________________________________________________
MultiOutputRegressor(estimator=XGBRegressor(base_score=None, booster=None,
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=0.8,
                                            eval_metric=['mae'], gamma=0.1,
                                            gpu_id=None, importance_type='gain',
                                            interaction_constraints=None,
                                            learning_rate=0.05,
                                            max_delta_step=None, max_depth=5,
                                            min_child_weight=1, missing=nan,
                                            monotone_constraints=None,
                                            n_estimators=2000, n_jobs=None

MSE = 195438.31
MAE = 322.0029
_______________________________________________________________________________
MultiOutputRegressor(estimator=LGBMRegressor(learning_rate=0.05,
                                             n_estimators=1000))
MSE = 200794.02645847137
MAE = 328.10686305154746
_______________________________________________________________________________
Keeping k-best features where k =  74
MultiOutputRegressor(estimator=StackingCVRegressor(meta_regressor=Ridge(),
                                                   random_state=42,
                                                   regressors=(LinearRegression(),
                                                               Ridge(),
                                                               ExtraTreesRegressor(n_estimators=1000,
                                                                                   random_state=0),
                                                               KNeighborsRegressor(n_neighb

In [23]:
week_daydiff_recording

Model     Run0     Run1  \
0   MultiOutputRegressor(estimator=StackingCVRegre... 393.1633 389.2529   
1   MultiOutputRegressor(estimator=LinearRegressio... 392.0614 389.1414   
2   MultiOutputRegressor(estimator=VotingRegressor... 392.2684 412.0591   
3         MultiOutputRegressor(estimator=LinearSVR()) 404.1888 398.3816   
4      MultiOutputRegressor(estimator=SGDRegressor()) 392.1370 389.3690   
5   MultiOutputRegressor(estimator=MLPRegressor(al... 398.0284 396.6797   
6               MultiOutputRegressor(estimator=SVR()) 401.4105 403.0958   
7             MultiOutputRegressor(estimator=NuSVR()) 402.7252 403.9042   
8     MultiOutputRegressor(estimator=BayesianRidge()) 392.5494 389.9266   
9   MultiOutputRegressor(estimator=DecisionTreeReg... 391.1190 536.1406   
10  MultiOutputRegressor(estimator=ElasticNetCV(cv... 396.3757 395.2282   
11  MultiOutputRegressor(estimator=LinearRegressio... 392.0614 389.1414   
12            MultiOutputRegressor(estimator=Ridge()) 392.1232 389.2048   
13      MultiOutputRegressor(estimator=KernelRidge()) 393.5116 390.8757   
14  MultiOutputRegressor(estimator=LassoCV(cv=5, r... 392.2933 389.9220   
15  MultiOutputRegressor(estimator=GaussianProcess... 392.0631 650.3834   
16  MultiOutputRegressor(estimator=ExtraTreesRegre... 392.0614 503.3852   
17  MultiOutputRegressor(estimator=KNeighborsRegre... 415.7768 418.9935   
18  MultiOutputRegressor(estimator=XGBRegressor(ba... 392.0400 473.7150   
19  MultiOutputRegressor(estimator=LGBMRegressor(l... 392.0614 427.7748   

        Run2       Run3       Run4        Run5       Run6      Run7      Run8  \
0   378.3177   378.9750   357.1340    363.2372   355.8393  346.4528  340.5452   
1   375.3262   373.8607   359.5793    352.8618   351.1825  348.3376  347.9781   
2   398.8054   395.6142   364.4511    375.5322   372.0915  360.4839  353.3242   
3   395.3387   394.1706   387.9182    382.3872   376.7891  371.6979  370.4439   
4   375.8764   374.7225   360.2124    353.3261   352.1703  349.1606  348.7653   
5   379.2440   385.4405   359.0942    381.0112   365.4367  368.1622  365.4271   
6   402.1129   403.4664   401.2565    400.3422   400.7216  401.0281  401.4635   
7   403.0544   404.1521   401.9042    401.1975   401.6198  401.8955  402.3173   
8   376.9555   375.7005   360.9038    354.1386   352.4458  348.9714  348.6827   
9   522.6976   546.4875   521.5537    589.0535   581.9138  548.8790  555.0596   
10  387.3971   386.3572   373.4747    365.6770   363.2125  359.0811  358.3922   
11  375.3262   373.8607   359.5793    352.8618   351.1825  348.3376  347.9781   
12  375.4721   374.0437   359.7478    352.9945   351.3089  348.4451  348.1120   
13  377.4458   376.1933   361.5277    359.8801   358.2233  353.7396  353.1689   
14  376.8305   375.0555   361.1863    354.2888   352.7311  349.4363  349.0204   
15 3117.3364 43783.0551 85674.3884 108177.5423 80104.0425 3480.9891 1160.4726   
16  482.2676   433.2569   381.6992    410.3959   386.5403  371.9042  359.4370   
17  410.0496   402.7710   379.0359    383.6408   374.7593  358.7160  352.6720   
18  473.7660   465.3932   406.8224    436.3018   407.5100  392.2632  383.7234   
19  421.2019   465.3471   419.1534    434.4734   419.3434  409.8720  399.0759   

       Run9    Run10    Run11    Run12    Run13    Run14    Run15    Run16  \
0  341.6938 329.3466 324.4779 316.2516 314.1807 311.1079 310.4340 310.3850   
1  348.6153 341.6925 338.1511 320.9740 320.9040 320.2948 320.3504 320.7994   
2  354.3717 341.7610 337.4328 324.7277 326.3939 327.8620 325.0902 326.6719   
3  370.2097 363.4960 360.3709 356.7061 354.4391 354.6799 354.5029 354.5282   
4  350.0322 343.0407 340.2707 323.6318 326.7003 324.7991 323.1972 324.2431   
5  380.1036 352.3456 350.2020 349.7106 355.9894 354.2584 382.6492 349.7762   
6  401.7148 401.0265 401.0690 400.7924 400.7162 400.7164 400.7172 400.7171   
7  402.6182 402.0120 402.1168 401.8826 401.8292 401.8293 401.8306 401.8313   
8  349.3502 342.7088 339.0019 322.1801 322.3726 321.8442 321.8690 32

In [25]:
week_daydiff_recording.to_csv('ScikitResultsWeekDayDiff02012021.csv')

### Weekly Difference

In [ ]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays','DailyAvg','DailyBusyness','AvgDailyDiff'])
remove=14
data = data.drop([x for x in range(remove)])
data = data.reset_index(drop=True)
lookback=20
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason','WeeklyAvg','MinSales','MaxSales',
                          'WeeklyBusyness','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff',
                                 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                                 14, 15, 16, 17, 18, 19,  
                        'WeeklyDifference']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
#df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
#df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

#df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
#df["DailyDifference"] = df.DailyDifference.astype(float)
df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

lb_data = diff_add_lookback(data, lookback, df,'WeeklyDifference')
lb_data = lb_data.reset_index(drop=True)

hotdata = onehotholidaydiff(lb_data, 'WeeklyDifference')
hotdata = hotdata.drop(columns=[14,15,16,17,18,19])

hot_numcols = len(hotdata.columns)
dataset = hotdata.values

lbset=lb_data.values
lb_numcols =  len(lb_data.columns)

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

In [26]:
X=dataset[:, 0:hot_numcols-1]
y=lbset[:, lb_numcols-7:lb_numcols]
X=X.astype(float)
y=y.astype(float)
scaler = preprocessing.RobustScaler()
X = scaler.fit_transform(X,y)

sys.stdout.flush()

clflist=[stack,LR,VR,linsvr,SGD , nn, svr, nusvr, bridge, dt, els,LR,ridge,kridge, 
         Lcv,  gpr, ETCModel, neigh, XGBModel, lgbm]  
#,
week_weekdiff_recording = pd.DataFrame(clflist,columns=['Model'])

scoring = {
        'mae': 'neg_mean_absolute_error',
        'mse' : 'neg_mean_squared_error',
        'custom': make_scorer(spcc, greater_is_better=True)
    }

j_arr = []
for j in range (74):
    print('Keeping k-best features where k = ', (j+1))
    mae_arr = []
    max_arr = []
    rmse_arr = []
    corr_arr = []

    for x in range(len(clflist)):
        corr_arr.append(0)
        mae_arr.append(0)
        rmse_arr.append(0)
        max_arr.append(0)
    i=0
    for clf in clflist:
            feat_reduction = SelectKBest(f_regression, k=j+1) 
            X_new = feat_reduction.fit_transform(X,y[:,0])
            print(clf) 
            X_train, X_test, y_train, y_test = train_test_split(X_new, y, test_size=221, random_state=42, shuffle=False)

            clf.fit(X_train, y_train)
            y_pred = clf.predict(X_test)
            
            meansq = keras.metrics.mean_squared_error(y_test.flatten(), y_pred.flatten()).numpy()
            meanabs = keras.metrics.mean_absolute_error(y_test.flatten(), y_pred.flatten()).numpy()
            print("MSE = "+str(meansq))
            print("MAE = "+str(meanabs))
            mae_arr[i]=meanabs
            i= i+1
            print('_______________________________________________________________________________')
    
    j_arr.append(j+1)
    week_weekdiff_recording['Run'+str(j)] = mae_arr

corr_arr = np.array(corr_arr)
print("COMPLETE")

train_df Shape: (1077, 54)
After encoding: (1077, 75)
Keeping k-best features where k =  1
MultiOutputRegressor(estimator=StackingCVRegressor(meta_regressor=Ridge(),
                                                   random_state=42,
                                                   regressors=(LinearRegression(),
                                                               Ridge(),
                                                               ExtraTreesRegressor(n_estimators=1000,
                                                                                   random_state=0),
                                                               KNeighborsRegressor(n_neighbors=7),
                                                               MLPRegressor(alpha=1e-05,
                                                                            hidden_layer_sizes=(5,
                                                                                                5,
                       

MSE = 165412.8706489314
MAE = 282.31660446507533
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 163013.07436066732
MAE = 280.9576264544594
_______________________________________________________________________________
MultiOutputRegressor(estimator=VotingRegressor(estimators=[('gb',
                                                            GradientBoostingRegressor(n_estimators=10,
                                                                                      random_state=1)),
                                                           ('rf',
                                                            RandomForestRegressor(n_estimators=10,
                                                                                  random_state=1)),
                                                           ('lr',
                                                            LinearRegression()),
      

MSE = 170028.2764289558
MAE = 290.14548217724206
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearSVR())
MSE = 160883.8569891436
MAE = 279.42477806076397
_______________________________________________________________________________
MultiOutputRegressor(estimator=SGDRegressor())
MSE = 161226.70546848394
MAE = 280.1232945231596
_______________________________________________________________________________
MultiOutputRegressor(estimator=MLPRegressor(alpha=1e-05,
                                            hidden_layer_sizes=(5, 5, 5, 5, 5),
                                            random_state=42, solver='lbfgs'))
MSE = 163067.87418660717
MAE = 281.6852670541641
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 163362.09992086093
MAE = 281.10691026758866
_______________________________________________________________________________
MultiOutpu

MSE = 164080.9434383635
MAE = 281.03549630009667
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 163000.80810809726
MAE = 280.5346041793486
_______________________________________________________________________________
MultiOutputRegressor(estimator=NuSVR())
MSE = 163251.00925103613
MAE = 281.3022918767449
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 157891.84118587253
MAE = 276.67779046532826
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 306239.25080904976
MAE = 399.6107045895281
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                    

MSE = 163252.3502375602
MAE = 281.30590738009954
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 157947.36823717022
MAE = 276.68471945051635
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 297195.77010058187
MAE = 396.5899676793794
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                                            random_state=0))
MSE = 157512.2357436326
MAE = 276.36897596530895
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 158669.52367418938
MAE = 277.55451852819
____________________________________________________________________

...

MSE = 143062.27143026594
MAE = 269.91157393209573
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearSVR())
MSE = 142283.41754640848
MAE = 260.70329358494206
_______________________________________________________________________________
MultiOutputRegressor(estimator=SGDRegressor())
MSE = 143713.27878506653
MAE = 263.7958741352206
_______________________________________________________________________________
MultiOutputRegressor(estimator=MLPRegressor(alpha=1e-05,
                                            hidden_layer_sizes=(5, 5, 5, 5, 5),
                                            random_state=42, solver='lbfgs'))
MSE = 253628.0539571694
MAE = 327.7335276677635
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 163220.7309570702
MAE = 281.2899249443303
_______________________________________________________________________________
MultiOutput

MSE = 200139.0054309463
MAE = 303.6826151777784
_______________________________________________________________________________
MultiOutputRegressor(estimator=SVR())
MSE = 163220.8315156192
MAE = 281.2900503320312
_______________________________________________________________________________
MultiOutputRegressor(estimator=NuSVR())
MSE = 163509.07476869132
MAE = 282.08369277885464
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 141040.63584150313
MAE = 261.0499350575846
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 275646.37717737554
MAE = 393.24508080155147
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                     

MSE = 163511.45271073235
MAE = 282.0860946428536
_______________________________________________________________________________
MultiOutputRegressor(estimator=BayesianRidge())
MSE = 141014.75835555614
MAE = 261.02587249885505
_______________________________________________________________________________
MultiOutputRegressor(estimator=DecisionTreeRegressor(criterion='mae',
                                                     random_state=0))
MSE = 297336.827250808
MAE = 409.62713639301876
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                                            random_state=0))
MSE = 139961.12943124512
MAE = 259.6680821700794
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 150858.7655007074
MAE = 276.3660059793147
____________________________________________________________________

MSE = 295767.3569702649
MAE = 411.21943115707825
_______________________________________________________________________________
MultiOutputRegressor(estimator=ElasticNetCV(cv=10, max_iter=100000,
                                            random_state=0))
MSE = 139963.41644280113
MAE = 259.6669418182446
_______________________________________________________________________________
MultiOutputRegressor(estimator=LinearRegression())
MSE = 150394.49542216244
MAE = 275.5201513892816
_______________________________________________________________________________
MultiOutputRegressor(estimator=Ridge())
MSE = 146960.34328626475
MAE = 270.0264032302098
_______________________________________________________________________________
MultiOutputRegressor(estimator=KernelRidge())
MSE = 146932.0604031075
MAE = 269.94881615366626
_______________________________________________________________________________
MultiOutputRegressor(estimator=LassoCV(cv=5, random_state=0))
MSE = 138867.3639116754
MAE

MSE = 147143.02450301909
MAE = 270.11106798567903
_______________________________________________________________________________
MultiOutputRegressor(estimator=LassoCV(cv=5, random_state=0))
MSE = 139153.80074509457
MAE = 258.19158585369973
_______________________________________________________________________________
MultiOutputRegressor(estimator=GaussianProcessRegressor())
MSE = 163829.06548318724
MAE = 281.9337121566197
_______________________________________________________________________________
MultiOutputRegressor(estimator=ExtraTreesRegressor(n_estimators=1000,
                                                   random_state=0))
MSE = 145965.76625459187
MAE = 267.39997923723337
_______________________________________________________________________________
MultiOutputRegressor(estimator=KNeighborsRegressor(n_neighbors=7))
MSE = 156631.72043373616
MAE = 286.1408357189029
_______________________________________________________________________________
MultiOutputRegressor(estim

In [27]:
week_weekdiff_recording

Model      Run0      Run1  \
0   MultiOutputRegressor(estimator=StackingCVRegre...  281.2499  282.3166   
1   MultiOutputRegressor(estimator=LinearRegressio...  280.9042  280.9576   
2   MultiOutputRegressor(estimator=VotingRegressor...  300.3518  300.2761   
3         MultiOutputRegressor(estimator=LinearSVR())  280.7488  280.7235   
4      MultiOutputRegressor(estimator=SGDRegressor())  280.8996  280.8682   
5   MultiOutputRegressor(estimator=MLPRegressor(al...  281.4440  280.3041   
6               MultiOutputRegressor(estimator=SVR())  281.1151  281.1074   
7             MultiOutputRegressor(estimator=NuSVR())  281.6625  281.6695   
8     MultiOutputRegressor(estimator=BayesianRidge())  280.8411  280.9352   
9   MultiOutputRegressor(estimator=DecisionTreeReg...  401.2031  401.2031   
10  MultiOutputRegressor(estimator=ElasticNetCV(cv...  280.5848  280.5613   
11  MultiOutputRegressor(estimator=LinearRegressio...  280.9042  280.9576   
12            MultiOutputRegressor(estimator=Ridge())  280.9011  280.9404   
13      MultiOutputRegressor(estimator=KernelRidge())  280.5420  280.5417   
14  MultiOutputRegressor(estimator=LassoCV(cv=5, r...  280.9186  280.9342   
15  MultiOutputRegressor(estimator=GaussianProcess... 5758.1333 5813.9805   
16  MultiOutputRegressor(estimator=ExtraTreesRegre...  366.6730  366.3651   
17  MultiOutputRegressor(estimator=KNeighborsRegre...  298.1605  297.5757   
18  MultiOutputRegressor(estimator=XGBRegressor(ba...  376.0861  351.2734   
19  MultiOutputRegressor(estimator=LGBMRegressor(l...  309.7125  309.7125   

         Run2        Run3        Run4       Run5      Run6      Run7  \
0    281.0846    279.4439    278.5332   278.7617  278.3224  278.2785   
1    280.0848    277.5219    277.5545   278.5156  276.6624  276.6352   
2    290.1455    287.1463    285.7890   288.1492  284.4385  283.3762   
3    279.4248    277.2798    277.3046   277.4123  276.4584  276.4407   
4    280.1233    277.5667    277.4886   278.3072  276.4046  276.4031   
5    281.6853    281.0355    281.5165   295.9946  285.7712  291.5589   
6    281.1069    280.5346    280.5396   280.8774  280.9583  280.9587   
7    281.7281    281.3023    281.3059   281.5058  281.6090  281.6096   
8    279.5469    276.6778    276.6847   276.6302  274.4294  274.4132   
9    407.3573    399.6107    396.5900   401.8778  393.6512  388.0813   
10   279.1451    276.3689    276.3690   276.2657  274.1793  274.1790   
11   280.0848    277.5219    277.5545   278.5156  276.6624  276.6352   
12   280.0714    277.5068    277.5323   278.4405  276.5725  276.5544   
13   279.6653    277.0917    277.1448   278.0567  276.1374  276.1356   
14   279.7044    276.5645    276.5513   277.1194  274.5083  274.5068   
15 41038.1286 113255.2785 112861.7390 93654.0572 6299.8334 6322.9085   
16   311.8821    303.6950    303.5951   299.4084  292.3113  292.1185   
17   305.1268    296.0594    296.1375   295.5594  289.4143  289.4143   
18   340.4930    323.4561    324.0893   316.2418  306.6812  308.6712   
19   330.2644    336.7553    336.7553   329.6014  324.5343  324.5343   

        Run8      Run9     Run10     Run11     Run12     Run13     Run14  \
0   277.8571  277.4055  277.0632  276.8242  276.9288  276.3027  276.3486   
1   276.6269  276.4734  276.4399  276.3631  276.4515  276.4178  276.3602   
2   283.6908  282.8114  282.7782  285.3807  283.4705  282.7264  282.4424   
3   276.4633  276.4648  276.3579  276.3632  276.3077  276.3475  276.2640   
4   276.3846  276.2364  276.0309  276.2014  276.1903  276.3467  276.0885   
5   284.5037  280.9025  283.1871  286.8097  283.0586  284.3871  281.9702   
6   280.9580  280.9918  280.9946  280.9927  281.0137  281.0140  281.0461   
7   281.6095  281.6376  281.6403  281.6389  281.6595  281.6603  281.6790   
8   274.4115  274.3483  274.2987  274.3450  274.4049  274.3998  274.2791   
9   396.9113  396.3387  400.6268  409.1009  397.9663  396.8146  390.2251   
10  274.1788  274.1402  274.1260  274.1275  274.1490  274.1490  274.0656   
11  2

In [28]:
week_weekdiff_recording.to_csv('ScikitResultsWeekWeekDiff02012021.csv')

In [14]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'WeeklyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'DailyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["DailyDifference"] = df.DailyDifference.astype(float)

diff_add_lookback(data, lookback, df,'DailyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'DailyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

X_new = SelectKBest(f_regression, k='all').fit(X,y)

dfscores = pd.DataFrame(X_new.scores_)
dfcolumns = pd.DataFrame(hotdata.columns)

#concat two dataframes for better visualization 
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']  #naming the dataframe columns
print(featureScores.nlargest(60,'Score'))  #print 10 best features
featureScores.to_csv('daydifferencefeatscores.csv',index=False)

train_df Shape: (1111, 37)
After encoding: (1090, 78)
              Specs    Score
15           Monday 428.7898
32                7 353.4626
20         Saturday 196.4893
25                0 195.0189
45     AvgDailyDiff 114.5196
44   WeeklyBusyness 104.1723
40        WeeklyAvg 102.5412
34                9  73.8060
37               12  72.7761
27                2  65.1181
30                5  61.8228
38               13  39.4944
19           Friday  25.9366
60              A11  22.3306
26                1  13.7845
72              A23  13.0638
49               A0  12.7196
46    AvgWeeklyDiff  10.7131
55               A6   8.0124
56               A7   6.7060
73              A24   6.5400
76              A27   6.3681
28                3   5.9108
33                8   5.2491
17        Wednesday   4.9616
35               10   4.5508
68              A19   4.3615
50               A1   3.6697
52               A3   3.5092
36               11   3.3961
29                4   3.3344
75              A2

In [15]:
np.random.seed(42)
# fix random seed for reproducibility
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])

for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0
    
df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason',
                         0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                         'WeeklyBusyness','2to5']]
df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)

lb_data = add_lookback(data, lookback, df)
lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholiday(lb_data)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,lb_data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

X_new = SelectKBest(f_regression, k='all').fit(X,y)

dfscores = pd.DataFrame(X_new.scores_)
dfcolumns = pd.DataFrame(hotdata.columns)

#concat two dataframes for better visualization 
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']  #naming the dataframe columns
print(featureScores.nlargest(60,'Score'))  #print 10 best features
featureScores.to_csv('actualfeatscores.csv',index=False)

train_df Shape: (1097, 47)
After encoding: (1097, 74)
              Specs     Score
40        WeeklyAvg 1476.1093
32                7 1048.4281
25                0  759.3703
42         MaxSales  302.5052
44   WeeklyBusyness  283.0770
0              Year  276.2937
38               13  270.4474
41         MinSales  249.9405
39         DailyAvg  249.4694
33                8  249.1481
26                1  246.6014
31                6  234.8282
20         Saturday  207.4213
14           Sunday  168.9591
43    DailyBusyness  160.0680
16          Tuesday   56.6720
15           Monday   41.8458
18         Thursday   34.9715
17        Wednesday   29.5130
68              A23   19.6140
56              A11   14.6314
71              A26   14.6314
37               12   10.5826
30                5   10.4038
49               A4    9.7053
46               A1    9.7020
51               A6    9.7020
27                2    9.5749
34                9    8.0843
11          October    7.4043
45              

In [16]:
# fix random seed for reproducibility
np.random.seed(8)
# load the dataset
dataframe = pd.read_csv('Data/RestaurantDataVets_All_2to5_Differenced.csv')
data = dataframe.drop(columns=['Index','Group','DMY','MissingPrevDays', 'DailyDifference','DiffDifference','2to5'])

lookback=14
dataframe_removed_lookback = data.drop([x for x in range(lookback)])
for i in range(lookback):
    dataframe_removed_lookback[i] = 1.0


df = dataframe_removed_lookback[['Year', 'Day', 'January','February',
                         'March','April','May','June','July',
                         'August', 'September', 'October', 'November',
                         'December','Sunday', 'Monday', 'Tuesday',
                         'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Holiday', 'Carnival', 
                         'LentFasting','Ramadan','ChristmasSeason', 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 
                         'DailyAvg','WeeklyAvg','MinSales','MaxSales','DailyBusyness',
                          'WeeklyBusyness','AvgDailyDiff','AvgWeeklyDiff','MinDailyDiff',
                         'MaxDailyDiff', 
                        'WeeklyDifference']]

df = df.reset_index(drop=True)

#Objects need to be converted to float due to missing values at load time.
df["DailyAvg"] = df.DailyAvg.astype(float)
df["WeeklyAvg"] = df.WeeklyAvg.astype(float)
df["MinSales"] = df.MinSales.astype(float)
df["MaxSales"] = df.MaxSales.astype(float)
df["DailyBusyness"] = df.DailyBusyness.astype(float)
df["WeeklyBusyness"] = df.WeeklyBusyness.astype(float)


df["AvgDailyDiff"] = df.AvgDailyDiff.astype(float)
df["AvgWeeklyDiff"] = df.AvgWeeklyDiff.astype(float)
df["MaxDailyDiff"] = df.MaxDailyDiff.astype(float)
df["MinDailyDiff"] = df.MinDailyDiff.astype(float)
df["WeeklyDifference"] = df.WeeklyDifference.astype(float)

diff_add_lookback(data, lookback, df,'WeeklyDifference')
#lb_data = lb_data.reset_index(drop=True)
hotdata = onehotholidaydiff(df,'WeeklyDifference')

hotdata = hotdata.drop([x for x in range(7)])
hotdata = hotdata.reset_index(drop=True)

cols = hotdata.columns[hotdata.dtypes.eq('object')]
hotdata[cols] = hotdata[cols].apply(pd.to_numeric, errors='coerce', axis=1)

numcols = len(hotdata.columns)
dataset = hotdata.values

print("train_df Shape:" ,data.shape)
print("After encoding:", hotdata.shape)

X=dataset[:, 0:numcols-1]
y=dataset[:, numcols-1]

X_new = SelectKBest(f_regression, k='all').fit(X,y)

dfscores = pd.DataFrame(X_new.scores_)
dfcolumns = pd.DataFrame(hotdata.columns)

#concat two dataframes for better visualization 
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']  #naming the dataframe columns
print(featureScores.nlargest(60,'Score'))  #print 10 best features
featureScores.to_csv('weekdifferencefeatscores.csv',index=False)

train_df Shape: (1111, 37)
After encoding: (1090, 78)
              Specs    Score
32                7 206.4237
60              A11  56.9747
75              A26  26.8010
46    AvgWeeklyDiff  26.3692
72              A23  16.2509
55               A6  14.8603
67              A18  10.8723
25                0   7.9179
64              A15   6.8268
38               13   6.0946
76              A27   5.4036
49               A0   5.4021
66              A17   3.1954
57               A8   2.6552
31                6   2.5109
74              A25   2.4687
24  ChristmasSeason   2.0138
1               Day   1.9226
53               A4   1.7417
4             March   1.6118
62              A13   1.1938
34                9   1.0752
37               12   1.0645
26                1   0.9818
56               A7   0.9373
51               A2   0.7835
63              A14   0.5985
27                2   0.5763
22      LentFasting   0.5123
65              A16   0.4882
36               11   0.4718
30                